In [1]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from scipy.stats import norm


## Ornstein Ukhlenbeck process has many represintations: $dX_t= -\theta\ X_t dt + \sigma dW_t$ or with drift term- 
## $$dX_t= -\theta\ (X_t - \mu) dt + \sigma dW_t$$

In [2]:
# mu=10
sigma=1
N=1000
n=100
t=20
theta=1
X0=3

h=1/n
t_=np.linspace(0,t,n*t+1)

paths=[]
for j in range(N):
    path=[X0]
    ksi=norm.rvs(loc=0, scale=np.sqrt(h), size=n*t)
    for i in range(1,n*t+1):
        xi=path[i-1]-1*theta*path[i-1]*h+sigma*ksi[i-1]
        path.append(xi)
    paths.append(path)


paths=np.array(paths)

# plot=go.Figure()
# for i in range(N):
#     plot.add_trace(go.Scatter(x=t_,y=paths[i],mode='lines',name=f'Path0{i}'))
# plot.show()

X2_bar=np.mean([path[-1] for path in paths])

print(abs(X2_bar-X0*np.exp(-theta*t)))

0.025614188170647163


In [3]:
def Ornstein_Uhlenbeck(mu,sigma,N,n,t,theta,X0):
    h=1/n
    t_=np.linspace(0,t,n*t+1)
    paths=[]
    for j in range(N):
        path=[X0]
        ksi=norm.rvs(loc=0, scale=np.sqrt(h), size=n*t)
        for i in range(1,n*t+1):
            xi=path[i-1]+theta*mu*h-1*theta*path[i-1]*h+sigma*ksi[i-1]
            path.append(xi)
        paths.append(path)
    return t_, np.array(paths)
    

In [4]:
mu=10
sigma=0.5
N=2000
n=100
t=2
theta=2
X0=3

h=1/n
t_=np.linspace(0,t,n*t+1)

paths=[]
for j in range(N):
    path=[X0]
    ksi=norm.rvs(loc=0, scale=np.sqrt(h), size=n*t)
    for i in range(1,n*t+1):
        xi=path[i-1]+theta*mu*h-1*theta*path[i-1]*h+sigma*ksi[i-1]
        path.append(xi)
    paths.append(path)


paths=np.array(paths)



# plot=go.Figure()
# for i in range(N):
#     plot.add_trace(go.Scatter(x=t_,y=paths[i],mode='lines',name=f'Path0{i}'))
# plot.show()



In [44]:
mu=20
sigma=4
N=20
n=100
t=20
theta=2
X0=5

paths=Ornstein_Uhlenbeck(mu,sigma,N,n,t,theta,X0)


plot=go.Figure()
for i in range(N):
    plot.add_trace(go.Scatter(x=paths[0],y=paths[1][i],mode='lines',name=f'Path0{i}'))
plot.show()

## OU Validation: Expectation, Variance, Covariance, 

In [36]:
mu=10
sigma=2
N=10000
n=100
t=20
theta=2
X0=1

t_, paths=Ornstein_Uhlenbeck(mu,sigma,N,n,t,theta,X0)

X10_sample=[path[int(t*n/2)] for path in paths]
X10_bar=np.mean(X10_sample)
X10_var=np.var(X10_sample)


X20_sample=([path[-1] for path in paths])
X20_bar=np.mean(X20_sample)
X20_var=np.var(X20_sample)


X10_X20_cov=np.cov(X10_sample,X20_sample)


print(f'difference between E(X_10) practical and theoretical:{abs(X10_bar-(X0-mu)*np.exp(-theta*t/2)-mu)}')
print(f'difference between E(X_20) practical and theoretical:{abs(X20_bar-(X0-mu)*np.exp(-theta*t)-mu)}')
print(f'difference between Var(X_10) practical and theoretical:{abs(X10_var-(sigma**2/(2*theta))*(1-np.exp(-2*theta*t/2)))}')
print(f'difference between Var(X_20) practical and theoretical:{abs(X20_var-(sigma**2/(2*theta))*(1-np.exp(-2*theta*t)))}')

print(f'difference between Cov(X_10,X_20) practical and theoretical:{abs(X10_X20_cov[0,1]-sigma**2/(2*theta)*(np.exp(-theta*t/2)-np.exp(-theta*1.5*t)))}')


print(X10_X20_cov)

difference between E(X_10) practical and theoretical:0.02198335583811506
difference between E(X_20) practical and theoretical:0.0008987024050455261
difference between Var(X_10) practical and theoretical:0.020822390569127602
difference between Var(X_20) practical and theoretical:0.007471838607917558
difference between Cov(X_10,X_20) practical and theoretical:0.000737065389760655
[[1.02092448e+00 7.37067451e-04]
 [7.37067451e-04 1.00757260e+00]]


# Vasicek model

In [7]:
def Vasichek(alpha, beta,sigma,N,n,t,X0):
    theta=beta
    mu=alpha/beta
    t_, paths=Ornstein_Uhlenbeck(mu,sigma,N,n,t,theta,X0)
    return t_, np.array(paths)

In [46]:
alpha=2
beta=1
sigma=0.5
N=100
n=100
t=20
X0=10

t_, paths=Vasichek(alpha,beta,sigma,N,n,t,X0)

plot=go.Figure()
for i in range(N):
    plot.add_trace(go.Scatter(x=t_,y=paths[i],mode='lines',name=f'Path0{i}'))
plot.show()

# 0.01*np.exp(-alpha*t)*np.exp(0.5*beta*t)+np.sqrt(1-np.exp(-2*alpha*t))*norm.rvs(loc=0, scale=np.sqrt(beta*t)) - честно, не помню, зачем я это добавил, но пусть будет


Vasicek validation

In [34]:
alpha=2
beta=1
sigma=0.5
N=10000
n=100
t=20
X0=10

t_, paths=Vasichek(alpha,beta,sigma,N,n,t,X0)

X10_sample=[path[int(t*n/2)] for path in paths]
X10_bar=np.mean(X10_sample)
X10_var=np.var(X10_sample)


X20_sample=([path[-1] for path in paths])
X20_bar=np.mean(X20_sample)
X20_var=np.var(X20_sample)


X10_X20_cov=np.cov(X10_sample,X20_sample)


print(f'difference between E(r_10) practical and theoretical:{abs(X10_bar-(X0-alpha/beta)*np.exp(-beta*t/2)-alpha/beta)}')
print(f'difference between E(r_20) practical and theoretical:{abs(X20_bar-(X0-alpha/beta)*np.exp(-beta*t)-alpha/beta)}')
print(f'difference between Var(r_10) practical and theoretical:{abs(X10_var-(sigma**2/(2*beta))*(1-np.exp(-2*beta*t/2)))}')
print(f'difference between Var(r_20) practical and theoretical:{abs(X20_var-(sigma**2/(2*beta))*(1-np.exp(-2*beta*t)))}')

print(f'difference between Cov(r_10,r_20) practical and theoretical:{abs(X10_X20_cov[0,1]-sigma**2/(2*beta)*(np.exp(-beta*t/2)-np.exp(-beta*1.5*t)))}')

difference between E(r_10) practical and theoretical:0.003259770537272333
difference between E(r_20) practical and theoretical:0.0030039899260176917
difference between Var(r_10) practical and theoretical:0.00021457040976331776
difference between Var(r_20) practical and theoretical:0.0003878948415042549
difference between Cov(r_10,r_20) practical and theoretical:0.0005214508183804292
